In [1]:
!pip install fbprophet==0.6

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 54.4/54.4 kB 2.2 MB/s eta 0:00:00
  Preparing metadata (setup.py) ... - \ done
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 91.8/91.8 kB 5.1 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 45.3/45.3 MB 37.3 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 1.8/1.8 MB 61.5 MB/s eta 0:00:00
  error: subprocess-exited-with-error
  
  × python setup.py bdist_wheel did not run successfully.
  │ exit code: 1
  ╰─> [42 lines of output]
      /tmp/pip-install-12cqun68/fbprophet_322a14ddb0b84110851b00ea6d181838/setup.py:10: DeprecationWarning: pkg_resources is deprecated as an API. See https://setuptools.pypa.io/en/latest/pkg_resources.html
        from pkg_resources import (
      Traceback (most recent call last):
        File "<string>", line 2, in <module>
        File "<pip-setuptools-caller>", line 34, in <module>
        File "/tmp/pip-install-12cqun68/fbprophet_322a14ddb0b84110851b00ea6d181838/setup.py", line 120, 

In [1]:
import pandas as pd
import numpy as np
from sklearn.metrics import mean_squared_error, r2_score, mean_absolute_error
from sklearn.model_selection import TimeSeriesSplit
from sklearn.preprocessing import MinMaxScaler
from sklearn.linear_model import LinearRegression
from sklearn.ensemble import RandomForestRegressor
from statsmodels.graphics.tsaplots import plot_pacf, plot_acf
# from fbprophet.plot import plot_plotly
#import prophet

import keras
from keras import layers 


In [2]:
df_stocks = pd.read_csv("data/stocks/ALOT.csv")

df_stocks["Date"] = pd.to_datetime(df_stocks.Date)
df_stocks.sort_values("Date", inplace=True)
# df_stocks.set_index("Date", inplace=True)
df_stocks

Date      Open      High       Low     Close  Adj Close   Volume
0    1981-10-01  0.000000  1.030303  1.030303  1.030303   0.465864    500.0
1    1981-10-02  0.000000  1.090909  1.030303  1.090909   0.493268   1700.0
2    1981-10-05  0.000000  1.131313  1.131313  1.131313   0.511537   2300.0
3    1981-10-06  0.000000  1.131313  1.131313  1.131313   0.511537    500.0
4    1981-10-07  1.131313  1.131313  1.131313  1.131313   0.511537      0.0
...         ...       ...       ...       ...       ...        ...      ...
9704 2020-03-26  8.250000  9.110000  8.250000  9.070000   9.070000  58800.0
9705 2020-03-27  8.640000  8.820000  7.940000  7.950000   7.950000  69200.0
9706 2020-03-30  7.900000  8.220000  7.410000  8.190000   8.190000  31000.0
9707 2020-03-31  8.050000  8.370000  7.540000  7.760000   7.760000  29600.0
9708 2020-04-01  7.360000  7.960000  6.940000  7.300000   7.300000  45600.0

[9709 rows x 7 columns]

In [3]:
df_stocks["High_s1"] = df_stocks["High"].shift(1)
df_stocks["Low_s1"] = df_stocks["Low"].shift(1)
df_stocks["Close_s1"] = df_stocks["Close"].shift(1)
df_stocks["delta_s1"] = (df_stocks["High"] - df_stocks["Low"]).shift(1)
df_stocks


Date      Open      High       Low     Close  Adj Close   Volume  \
0    1981-10-01  0.000000  1.030303  1.030303  1.030303   0.465864    500.0   
1    1981-10-02  0.000000  1.090909  1.030303  1.090909   0.493268   1700.0   
2    1981-10-05  0.000000  1.131313  1.131313  1.131313   0.511537   2300.0   
3    1981-10-06  0.000000  1.131313  1.131313  1.131313   0.511537    500.0   
4    1981-10-07  1.131313  1.131313  1.131313  1.131313   0.511537      0.0   
...         ...       ...       ...       ...       ...        ...      ...   
9704 2020-03-26  8.250000  9.110000  8.250000  9.070000   9.070000  58800.0   
9705 2020-03-27  8.640000  8.820000  7.940000  7.950000   7.950000  69200.0   
9706 2020-03-30  7.900000  8.220000  7.410000  8.190000   8.190000  31000.0   
9707 2020-03-31  8.050000  8.370000  7.540000  7.760000   7.760000  29600.0   
9708 2020-04-01  7.360000  7.960000  6.940000  7.300000   7.300000  45600.0   

       High_s1    Low_s1  Close_s1  delta_s1  
0          NaN       NaN       NaN       NaN  
1     1.030303  1.030303  1.030303  0.000000  
2     1.090909  1.030303  1.090909  0.060606  
3     1.131313  1.131313  1.131313  0.000000  
4     1.131313  1.131313  1.131313  0.000000  
...        ...       ...       ...       ...  
9704  8.470000  7.410000  8.360000  1.060000  
9705  9.110000  8.250000  9.070000  0.860000  
9706  8.820000  7.940000  7.950000  0.880000  
9707  8.220000  7.410000  8.190000  0.810000  
9708  8.370000  7.540000  7.760000  0.830000  

[9709 rows x 11 columns]

In [6]:
features = ["Open", "High_s1", "Low_s1", "Close_s1", "delta_s1"]
target = "Close"
days = 10
min_date = df_stocks.Date.min()
max_date = df_stocks.Date.max()
min_date, max_date


(Timestamp('1981-10-01 00:00:00'), Timestamp('2020-04-01 00:00:00'))

In [7]:
n_splits = (max_date - min_date).days // days
print(n_splits)
    
res_ls = []
start_date = min_date
    
i = 0
df_train = df_stocks.iloc[i:i+days-2]
df_test = df_stocks.iloc[i+days-2:i+days]
df_train

1406


Date      Open      High       Low     Close  Adj Close  Volume  \
0 1981-10-01  0.000000  1.030303  1.030303  1.030303   0.465864   500.0   
1 1981-10-02  0.000000  1.090909  1.030303  1.090909   0.493268  1700.0   
2 1981-10-05  0.000000  1.131313  1.131313  1.131313   0.511537  2300.0   
3 1981-10-06  0.000000  1.131313  1.131313  1.131313   0.511537   500.0   
4 1981-10-07  1.131313  1.131313  1.131313  1.131313   0.511537     0.0   
5 1981-10-08  0.000000  1.131313  1.090909  1.090909   0.493268  4200.0   
6 1981-10-09  0.000000  1.131313  1.131313  1.131313   0.511537  1100.0   
7 1981-10-12  0.000000  1.070707  1.070707  1.070707   0.484134  3000.0   

    High_s1    Low_s1  Close_s1  delta_s1  
0       NaN       NaN       NaN       NaN  
1  1.030303  1.030303  1.030303  0.000000  
2  1.090909  1.030303  1.090909  0.060606  
3  1.131313  1.131313  1.131313  0.000000  
4  1.131313  1.131313  1.131313  0.000000  
5  1.131313  1.131313  1.131313  0.000000  
6  1.131313  1.090909  1.090909  0.040404  
7  1.131313  1.131313  1.131313  0.000000

In [5]:
from tqdm import tqdm
import pandas as pd

def train_walk_forward(model, df_stocks):
    features = ["Open", "High_s1", "Low_s1", "Close_s1", "delta_s1"]
    target = "Close"
    days = 10
    min_date = df_stocks.Date.min()
    max_date = df_stocks.Date.max()
    
    n_splits = (max_date - min_date).days // days
    
    res_ls = []
    start_date = min_date
    
    for i in tqdm(range(0, len(df_stocks), 2)):        
        df_train = df_stocks.iloc[i:i+days-2]
        df_test = df_stocks.iloc[i+days-2:i+days]

        if df_train.empty or df_test.empty:
            break
        
#         display(df_train.Date.tolist())
        
        model.fit(df_train[features], df_train[target])
        df_test["predict"] = model.predict(df_test[features])
        res_ls.append(df_test)
            
    return pd.concat(res_ls)

In [6]:
import plotly.graph_objs as go
import plotly.offline as py

def plot_plotly(df_test, model_name="Linear Regression"):
    forecast = df_test[['Date']].copy()
    forecast['yhat'] = df_test['predict']
    forecast['yhat_lower'] = forecast['yhat'] - 10
    forecast['yhat_upper'] = forecast['yhat'] + 10

    fig = go.Figure()

    fig.add_trace(go.Scatter(x=df_test['Date'], y=df_test["Close"], mode='markers', name='Actual'))

    fig.add_trace(go.Scatter(x=forecast['Date'], y=forecast['yhat'], mode='lines', name='Predicted'))

    fig.add_trace(go.Scatter(
        x=forecast['Date'].tolist() + forecast['Date'].tolist()[::-1],
        y=forecast['yhat_upper'].tolist() + forecast['yhat_lower'].tolist()[::-1],
        fill='toself',
        fillcolor='rgba(0,100,80,0.2)',
        line=dict(color='rgba(255,255,255,0)'),
        hoverinfo="skip",
        showlegend=False,
        name='Confidence Interval'
    ))

    fig.update_layout(
        title=f"{model_name} Forecast with Confidence Interval",
        xaxis_title="Date",
        yaxis_title="Value",
        showlegend=True
    )

    py.iplot(fig)

In [7]:
import warnings
warnings.filterwarnings("ignore")

model = LinearRegression()
df_test = train_walk_forward(model, df_stocks.dropna())

100%|█████████▉| 4849/4853 [00:23<00:00, 204.41it/s]


In [8]:
len(df_test) - df_test[df_test.predict.abs() < 1000].__len__()

62

There are 58 points (outliers) that are pretty inconvenient to keep. Those should've been explored and treated in a proper way, but since there was not that much time We will skip it for now. Because of those points our graphic's scale couldn't show any useful information for us

In [9]:
plot_plotly(df_test[df_test.predict.abs() < 1000])

In [10]:
model = RandomForestRegressor()
df_test = train_walk_forward(model, df_stocks.dropna())

100%|█████████▉| 4849/4853 [14:20<00:00,  5.64it/s]


In [11]:
plot_plotly(df_test, "Random Forest")

In [12]:
from sklearn.preprocessing import MinMaxScaler
scaler = MinMaxScaler()
df_stocks_scaled = df_stocks.copy().set_index("Date")
scaler.fit(df_stocks_scaled.dropna())
df_stocks_scaled = pd.DataFrame(scaler.transform(df_stocks_scaled.dropna()), columns=df_stocks_scaled.columns)

df_stocks_scaled["Date"] = df_stocks.dropna()["Date"]

In [13]:
from tensorflow.keras import Sequential
from tensorflow.keras.layers import LSTM, Dropout, Dense, Activation

class LSTM_DNN:
    def __init__(self):
        model = Sequential()
        model.add(LSTM(units = 50, input_shape = (5, 1), return_sequences = True))
        model.add(Dropout(0.5))
        model.add(LSTM(256))
        model.add(Dropout(0.5))
        model.add(Dense(1))
        model.add(Activation("linear"))
        model.compile(loss="mse", optimizer="adam")
        model.summary()
        self.model = model
        
    def fit(self, features, target):
        self.model.fit(features, target)
    def predict(self, features):
        return self.model.predict(features)
    
# LSTM_DNN()

In [14]:
model = LSTM_DNN()
df_test = train_walk_forward(model, df_stocks_scaled)

Model: "sequential"

┏━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━┳━━━━━━━━━━━━━━━━━━━━━━━━┳━━━━━━━━━━━━━━━┓
┃ Layer (type)                    ┃ Output Shape           ┃       Param # ┃
┡━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━╇━━━━━━━━━━━━━━━━━━━━━━━━╇━━━━━━━━━━━━━━━┩
│ lstm (LSTM)                     │ (None, 5, 50)          │        10,400 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ dropout (Dropout)               │ (None, 5, 50)          │             0 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ lstm_1 (LSTM)                   │ (None, 256)            │       314,368 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ dropout_1 (Dropout)             │ (None, 256)            │             0 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ dense (Dense)                   │ (None, 1)              │           257 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ activation (Activation)         │ (None, 1)              │             0 │
└─────────────────────────────────┴────────────────────────┴───────────────┘

 Total params: 325,025 (1.24 MB)

 Trainable params: 325,025 (1.24 MB)

 Non-trainable params: 0 (0.00 B)

...

100%|█████████▉| 4847/4853 [11:16<00:00,  7.38it/s]

1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 25ms/step - loss: 0.0068
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 18ms/step


100%|█████████▉| 4848/4853 [11:16<00:00,  7.18it/s]

1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 24ms/step - loss: 0.0041
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 17ms/step


100%|█████████▉| 4849/4853 [11:16<00:00,  7.17it/s]


In [15]:
scaler.fit(df_stocks[["Close"]])

MinMaxScaler()

In [16]:
# df_test["predict"] = 
# df_test
df_test["predict"] = scaler.inverse_transform(df_test[["predict"]])
df_test["Close"] = scaler.inverse_transform(df_test[["Close"]])
# df_test[["predict"]]
# df_test["Close"] = scaler.inverse_transform(df_test[["Close"]].values)

In [17]:
plot_plotly(df_test, "LSTM_DNN")
# df_test